In [0]:
# Run this cell to mount your Google Drive.
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
# Uncomment if you want to use Symbolic link
!ln -s /content/drive/My\ Drive/project_last/darknet/ /myDrive
!ls /myDrive

20190712_171207.mp4  CMakeLists.txt	     Makefile
3rdparty	     darknet		     net_cam_v3.sh
appveyor.yml	     DarknetConfig.cmake.in  obj
backup		     darknet.py		     predictions.jpg
bad.list	     darknet_video.py	     README.md
build		     data		     results
build.ps1	     image_yolov2.sh	     scripts
build.sh	     image_yolov3.sh	     src
cfg		     include		     test.mp4
chart.png	     json_mjpeg_streams.sh   video_v2.sh
cmake		     LICENSE		     video_yolov3.sh


In [0]:
%cd /myDrive

/content/drive/My Drive/project_last/darknet


In [0]:
#Changing the variables to include OpenCV and GPU in the Makefile
%cd /myDrive
!sed -i 's/OPENCV=0/OPENCV=1/g' Makefile
!sed -i 's/GPU=0/GPU=1/g' Makefile
#!sed -i 's/CUDNN=0/CUDNN=1/g' Makefile

/content/drive/My Drive/project_last/darknet


In [0]:
!cat Makefile

GPU=1
CUDNN=0
CUDNN_HALF=0
OPENCV=1
AVX=0
OPENMP=1
LIBSO=0
ZED_CAMERA=0

# set GPU=1 and CUDNN=1 to speedup on GPU
# set CUDNN_HALF=1 to further speedup 3 x times (Mixed-precision on Tensor Cores) GPU: Volta, Xavier, Turing and higher
# set AVX=1 and OPENMP=1 to speedup on CPU (if error occurs then set AVX=0)

DEBUG=0

ARCH= -gencode arch=compute_30,code=sm_30 \
      -gencode arch=compute_35,code=sm_35 \
      -gencode arch=compute_50,code=[sm_50,compute_50] \
      -gencode arch=compute_52,code=[sm_52,compute_52] \
	  -gencode arch=compute_61,code=[sm_61,compute_61]

OS := $(shell uname)

# Tesla V100
# ARCH= -gencode arch=compute_70,code=[sm_70,compute_70]

# GeForce RTX 2080 Ti, RTX 2080, RTX 2070, Quadro RTX 8000, Quadro RTX 6000, Quadro RTX 5000, Tesla T4, XNOR Tensor Cores
# ARCH= -gencode arch=compute_75,code=[sm_75,compute_75]

# Jetson XAVIER
# ARCH= -gencode arch=compute_72,code=[sm_72,compute_72]

# GTX 1080, GTX 1070, GTX 1060, GTX 1050, GTX 1030, Titan Xp, Tesla P40, Tesl

In [0]:
!apt-get install libopencv-dev

Reading package lists... Done
Building dependency tree       
Reading state information... Done
libopencv-dev is already the newest version (3.2.0+dfsg-4ubuntu0.1).
The following package was automatically installed and is no longer required:
  libnvidia-common-410
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 4 not upgraded.


In [0]:
!make

chmod +x *.sh
g++ -std=c++11 -Iinclude/ -I3rdparty/stb/include -DOPENCV `pkg-config --cflags opencv` -DGPU -I/usr/local/cuda/include/ -Wall -Wfatal-errors -Wno-unused-result -Wno-unknown-pragmas -fPIC -Ofast -DOPENCV -fopenmp -DGPU -c ./src/image_opencv.cpp -o obj/image_opencv.o
./src/image_opencv.cpp: In function ‘void draw_detections_cv_v3(mat_cv*, detection*, int, float, char**, image**, int, int)’:
./src/image_opencv.cpp:896:23: warning: variable ‘rgb’ set but not used [-Wunused-but-set-variable]
                 float rgb[3];
                       ^~~
g++ -std=c++11 -Iinclude/ -I3rdparty/stb/include -DOPENCV `pkg-config --cflags opencv` -DGPU -I/usr/local/cuda/include/ -Wall -Wfatal-errors -Wno-unused-result -Wno-unknown-pragmas -fPIC -Ofast -DOPENCV -fopenmp -DGPU -c ./src/http_stream.cpp -o obj/http_stream.o
./src/http_stream.cpp: In member function ‘bool JSON_sender::write(const char*)’:
./src/http_stream.cpp:228:21: warning: unused variable ‘n’ [-Wunused-variable]
           

In [0]:
%cd /myDrive

/content/drive/My Drive/project_last/darknet


In [0]:
!./darknet detector train /myDrive/build/darknet/x64/data/obj.data /myDrive/build/darknet/x64/cfg/yolo-obj.cfg /myDrive/build/darknet/x64/backup/yolo-obj_last.weights -dont_show

yolo-obj
   layer   filters  size/strd(dil)      input                output
   0 conv     32      3 x 3/ 1    416 x 416 x   3  ->  416 x 416 x  32 0.299 BF
   1 conv     64      3 x 3/ 2    416 x 416 x  32  ->  208 x 208 x  64 1.595 BF
   2 conv     32      1 x 1/ 1    208 x 208 x  64  ->  208 x 208 x  32 0.177 BF
   3 conv     64      3 x 3/ 1    208 x 208 x  32  ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1
   5 conv    128      3 x 3/ 2    208 x 208 x  64  ->  104 x 104 x 128 1.595 BF
   6 conv     64      1 x 1/ 1    104 x 104 x 128  ->  104 x 104 x  64 0.177 BF
   7 conv    128      3 x 3/ 1    104 x 104 x  64  ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5
   9 conv     64      1 x 1/ 1    104 x 104 x 128  ->  104 x 104 x  64 0.177 BF
  10 conv    128      3 x 3/ 1    104 x 104 x  64  ->  104 x 104 x 128 1.595 BF
  11 Shortcut Layer: 8
  12 conv    256      3 x 3/ 2    104 x 104 x 128  ->   52 x  52 x 256 1.595 BF
  13 conv    128      1 x 1/ 1     52 x  52 x 256  -> 

In [0]:
%cd /myDrive
!./darknet detector test /myDrive/build/darknet/x64/data/obj.data  /myDrive/build/darknet/x64/cfg/yolo-obj.cfg  /myDrive/build/darknet/x64/backup/yolo-obj_final.weights /myDrive/build/darknet/x64/data/multi1.jpg

/content/drive/My Drive/project_last/darknet
   layer   filters  size/strd(dil)      input                output
   0 conv     32      3 x 3/ 1    416 x 416 x   3  ->  416 x 416 x  32 0.299 BF
   1 conv     64      3 x 3/ 2    416 x 416 x  32  ->  208 x 208 x  64 1.595 BF
   2 conv     32      1 x 1/ 1    208 x 208 x  64  ->  208 x 208 x  32 0.177 BF
   3 conv     64      3 x 3/ 1    208 x 208 x  32  ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1
   5 conv    128      3 x 3/ 2    208 x 208 x  64  ->  104 x 104 x 128 1.595 BF
   6 conv     64      1 x 1/ 1    104 x 104 x 128  ->  104 x 104 x  64 0.177 BF
   7 conv    128      3 x 3/ 1    104 x 104 x  64  ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5
   9 conv     64      1 x 1/ 1    104 x 104 x 128  ->  104 x 104 x  64 0.177 BF
  10 conv    128      3 x 3/ 1    104 x 104 x  64  ->  104 x 104 x 128 1.595 BF
  11 Shortcut Layer: 8
  12 conv    256      3 x 3/ 2    104 x 104 x 128  ->   52 x  52 x 256 1.595 BF
  13 conv    128  

In [0]:
# Apparently we need to install this so that OpenCV can work without any issues
# when we are making the file
!apt-get install libopencv-dev

Reading package lists... Done
Building dependency tree       
Reading state information... Done
libopencv-dev is already the newest version (3.2.0+dfsg-4ubuntu0.1).
The following package was automatically installed and is no longer required:
  libnvidia-common-410
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 4 not upgraded.


In [0]:
# Upload the video you want to use for object detection
# Please use a filename without spaces like test.mp4 etc.
%cd /myDrive
from google.colab import files
uploaded = files.upload() 
for name, data in uploaded.items():
  with open(name, 'wb') as f:
    f.write(data)
    print ('saved file', name)

/content/drive/My Drive/project_last/darknet


In [0]:
# And finally run it! Please check if you have given the right video file name

%cd /myDrive
!./darknet detector demo /myDrive/build/darknet/x64/data/obj.data  /myDrive/build/darknet/x64/cfg/yolo-obj.cfg  /myDrive/build/darknet/x64/backup/yolo-obj_final.weights -dont_show  /myDrive/Test-video.mp4 -i 0 -out_filename res.avi

/content/drive/My Drive/project_last/darknet
Demo
   layer   filters  size/strd(dil)      input                output
   0 conv     32      3 x 3/ 1    416 x 416 x   3  ->  416 x 416 x  32 0.299 BF
   1 conv     64      3 x 3/ 2    416 x 416 x  32  ->  208 x 208 x  64 1.595 BF
   2 conv     32      1 x 1/ 1    208 x 208 x  64  ->  208 x 208 x  32 0.177 BF
   3 conv     64      3 x 3/ 1    208 x 208 x  32  ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1
   5 conv    128      3 x 3/ 2    208 x 208 x  64  ->  104 x 104 x 128 1.595 BF
   6 conv     64      1 x 1/ 1    104 x 104 x 128  ->  104 x 104 x  64 0.177 BF
   7 conv    128      3 x 3/ 1    104 x 104 x  64  ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5
   9 conv     64      1 x 1/ 1    104 x 104 x 128  ->  104 x 104 x  64 0.177 BF
  10 conv    128      3 x 3/ 1    104 x 104 x  64  ->  104 x 104 x 128 1.595 BF
  11 Shortcut Layer: 8
  12 conv    256      3 x 3/ 2    104 x 104 x 128  ->   52 x  52 x 256 1.595 BF
  13 conv    

In [0]:
!./darknet detector map /myDrive/build/darknet/x64/data/obj.data  /myDrive/build/darknet/x64/cfg/yolo-obj.cfg  /myDrive/build/darknet/x64/backup/yolo-obj_final.weights

   layer   filters  size/strd(dil)      input                output
   0 conv     32      3 x 3/ 1    416 x 416 x   3  ->  416 x 416 x  32 0.299 BF
   1 conv     64      3 x 3/ 2    416 x 416 x  32  ->  208 x 208 x  64 1.595 BF
   2 conv     32      1 x 1/ 1    208 x 208 x  64  ->  208 x 208 x  32 0.177 BF
   3 conv     64      3 x 3/ 1    208 x 208 x  32  ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1
   5 conv    128      3 x 3/ 2    208 x 208 x  64  ->  104 x 104 x 128 1.595 BF
   6 conv     64      1 x 1/ 1    104 x 104 x 128  ->  104 x 104 x  64 0.177 BF
   7 conv    128      3 x 3/ 1    104 x 104 x  64  ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5
   9 conv     64      1 x 1/ 1    104 x 104 x 128  ->  104 x 104 x  64 0.177 BF
  10 conv    128      3 x 3/ 1    104 x 104 x  64  ->  104 x 104 x 128 1.595 BF
  11 Shortcut Layer: 8
  12 conv    256      3 x 3/ 2    104 x 104 x 128  ->   52 x  52 x 256 1.595 BF
  13 conv    128      1 x 1/ 1     52 x  52 x 256  ->   52 x  5